
 __Scientific Computing, TU Berlin, WS 2019/2020, Lecture 25__

 Jürgen Fuhrmann, WIAS Berlin



# Nonlinear systems

In [ ]:
using Printf
using VoronoiFVM
using  Plots
using Printf
injupyter()=isdefined(Main, :IJulia) && Main.IJulia.inited




## The method

### Construction of control volumes

- Start  with a  triangulation  of a  polygonal  domain (intervals  in
  1D,triangles in 2D,  tetrahedra in 3D).

- Join triangle  circumcenters by  lines $\rightarrow$  create Voronoi
  cells which  can serve  as control  volumes, akin  to representative
  elementary volumes (REV) used to derive conservation laws.


<img src="trivoro.png" width="35%">


- Black + green: triangle nodes
- Gray: triangle edges
- Blue: triangle circumcenters
- Red: Boundaries of Voronoi cells



## Condition on triangulation

- There is a 1:1 incidence between triangulation nodes
  and Voronoi cells.  Moreover, the angle between  the interface between
  two Voronoi  cells and the  edge between their corresponding  nodes is
  $\frac\pi2$.

- Requires (in  2D) that sums  of angles  opposite to
  triangle edges are less than $\pi$ and that angles opposite to boudary
  edges are less than $\frac\pi2$.

- "boundary conforming Delaunay property". It has different equivalent definitions
  and analogues in 3D.

- Construction:
    - "by hand" (or script) from tensor product meshes
    - Mesh generators: Triangle, TetGen




## The discretization approach

- Use Voronoi cells as REVs aka control volumes aka finite volume cells.

<img src="vor.png" width="35%">


- Given  a  continuity  equation  $\nabla\cdot \vec  j=0$  in  a  domain
  $\Omega$,  integrate  this  over   a  contol  volume  $\omega_k$  with
  associated node $\vec x_k$ and apply Gauss theorem:


  \begin{align*}
    0&=\int_{\omega_k} \nabla\cdot  \vec j \ d\omega
       =\int_{\partial\omega_k} \vec j\cdot \vec n ds\\
     &=\sum_{l\in N_k} \int_{\omega_k\cap \omega_l} \vec j\cdot \vec n ds + \int_{\partial\omega_k\cap \partial\Omega} \vec j\cdot \vec n ds\\
     &\approx \sum_{l\in N_k} \frac{\sigma_{kl}}{h_{kl}}g(u_k, u_l)+ \gamma_k b(u_k)
  \end{align*}


- Here, $N_k$ is the set of neighbor control volumes, $\sigma_{kl}=|\omega_k\cap \omega_l|$, $h_{kl}=|\vec x_k -\vec x_l|$, $\gamma_k=|\partial\omega_k\cap \partial\Omega|$,  where  $|\cdot|$ denotes the measure (length resp. area) of a geometrical entity.



## Flux functions


For instance, for the diffusion flux $\vec j=-D\vec\nabla u$, we use $g(u_k, u_l)=D(u_k -u_l)$.

For a convective diffusion flux $\vec j = -D\vec \nabla u + u \vec v$, one can chose the upwind flux

\begin{align*}
g(u_k, u_l)=D(u_k -u_l) +
v_{kl}\begin{cases}
u_k,& v_{kl}>0\\
u_l,& v_{kl}\leq 0,
\end{cases}
\end{align*}

where $v_{kl}=\frac{h_{kl}}{\sigma_{kl}}\int_{\omega_k\cap \omega_l} \vec v \cdot \vec n_{kl} \ ds$
Fluxes also can depend nonlinearily on $u$.



For Diffusion flux $\vec j = -D\vec \nabla u^m\vec v$, we can choose the
flux $g(u_k, u_l)=D(u_k^m -u_l^m)$.




## Software API and implementation

The entities describing the discrete system can be subdivided into two categories:
- geometrical data: $|\omega_k|, \gamma_k, \sigma_{kl}, h_{kl}$ together with the connectivity information of the triangles
- physical data: the number $m$ and the functions $s,g,r,b,f$ describing the particular problem.

This structure allows to describe the problem to be solved by data derived from the discretization grid and by the functions describing the physics, giving rise to a software API.

The solution of the nonlinear systems of equations can be performed by Newton's method combined with various direct and iterative linear solvers.

The generic programming capabilities of Julia allow for an implementation of the method which results in an API which consists in  the implementation of functions $s,g,r,b,f$ without the need to write code for their derivatives.


## Examples

For the following examples,  we always start with an initival value and
watch the evolution of the isolated system. Isolation is achieved by setting
homogeneous Neumann boundary conditions, which don't occur in the discrete formulation
and therefore done have to be set explicitely.


### Diffusion problem $\partial_t u - \nabla\cdot D\nabla u=0$

In [ ]:
function diffusion(;n=1000, nt=100, tstep0=1.0e-3, D=1.0, dtgrowth=1.0)

    # Grid on interval 0.1
    X=collect(0:1.0/n:1)
    grid=VoronoiFVM.Grid(X)

    # Diffusion flux between neigboring control volumes
    function flux!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        f[1]=D*(uk[1]-ul[1])
    end

    # Storage term (under time derivative)
    function storage!(f,u,node,data)
        f[1]=u[1]
    end

    # Initial value
    fpeak(x)=exp(-100*(x-0.25)^2)

    # Create a physics structure
    physics=VoronoiFVM.Physics(
        flux=flux!,
        storage=storage!)

    sys=VoronoiFVM.DenseSystem(grid,physics)
    enable_species!(sys,1,[1])
    # Assume homogeneous Neumann boundary conditions, so do nothig

    # Create a solution array
    inival=unknowns(sys)
    solution=unknowns(sys)

    # Broadcast the initial value
    inival[1,:].=map(x->fpeak(x),X)

    # Run time evolution and plot
    time=0.0
    tstep=tstep0
    @gif for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,tstep=tstep)
        inival.=solution
        plot(X,solution[1,:],
             title="time=$(@sprintf("%.4f",time))",
             xlabel="x",ylabel="y",
             ylims=(0,1))
        tstep*=dtgrowth
    end
end

In [ ]:
injupyter()&& diffusion()


We observe an re-distribution of species while keeping the integral over the solution
constant until a final steady state is reached.


### Reaction-diffusion problem $\partial_t u - \nabla\cdot D\nabla u + R u=0$

In [ ]:
function reaction_diffusion(;n=1000,tstep0=1.0e-3, nt=100, D=1.0, R=1.0, dtgrowth=1.0)

    # Grid on interval 0.1
    X=collect(0:1.0/n:1)
    grid=VoronoiFVM.Grid(X)

    # Diffusion flux between neigboring control volumes
    function flux!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        f[1]=D*(uk[1]-ul[1])
    end

    # Storage term (under time derivative)
    function storage!(f,u,node,data)
        f[1]=u[1]
    end

    # Reaction term
    function reaction!(f,u,node,data)
        f[1]=R*u[1]
    end

    # Initial value
    fpeak(x)=exp(-100*(x-0.25)^2)

    # Create a physics structure
    physics=VoronoiFVM.Physics(
        flux=flux!,
        reaction=reaction!,
        storage=storage!)

    sys=VoronoiFVM.DenseSystem(grid,physics)
    enable_species!(sys,1,[1])
    # Assume homogeneous Neumann boundary conditions, so do nothig

    # Create a solution array
    inival=unknowns(sys)
    solution=unknowns(sys)

    # Broadcast the initial value
    inival[1,:].=map(x->fpeak(x),X)

    # Run time evolution and plot
    time=0.0
    tstep=tstep0
    @gif for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,tstep=tstep)
        plot(X,solution[1,:],
             title="time=$(@sprintf("%.4f",time))",
             xlabel="x",ylabel="y",
             ylims=(0,1))
        inival.=solution
        tstep*=dtgrowth
    end
end

In [ ]:
injupyter()&& reaction_diffusion()


We observe an re-distribution of species. It is accompanied by "eating" stuff
away due to the reaction term.


### Convection-Diffusion  problem $\partial_t u - \nabla\cdot( D\nabla u - u \vec v) =0$

In [ ]:
function convection_diffusion(;n=50,tstep0=1.0e-3, nt=100, D=0.01, v=10.0, dtgrowth=1.0, centered=true, expfit=false)

    # Grid on interval 0.1
    X=collect(0:1.0/n:1)
    grid=VoronoiFVM.Grid(X)

    B(x)=x/(exp(x)-1)
    # Diffusion flux between neigboring control volumes
    function flux!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        h=edgelength(edge)
        if centered
            f[1]=D*(uk[1]-ul[1])+ v*h*0.5*(uk[1]+ul[1])
        elseif expfit
            f[1]=D*(B(-v*h/D)*uk[1]- B(v*h/D)*ul[1])
        else
            f[1]=D*(uk[1]-ul[1])+ ( v>0.0 ? v*h*uk[1] : v*h*ul[1] )
        end
    end

    # Storage term (under time derivative)
    function storage!(f,u,node,data)
        f[1]=u[1]
    end

    # Initial value
    fpeak(x)=exp(-100*(x-0.25)^2)

    # Create a physics structure
    physics=VoronoiFVM.Physics(
        flux=flux!,
        storage=storage!)

    sys=VoronoiFVM.DenseSystem(grid,physics)
    enable_species!(sys,1,[1])
    # Assume homogeneous Neumann boundary conditions, so do nothig

    # Create a solution array
    inival=unknowns(sys)
    solution=unknowns(sys)

    # Broadcast the initial value
    inival[1,:].=map(x->fpeak(x),X)

    # Run time evolution and plot
    time=0.0
    tstep=tstep0
    @gif for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,tstep=tstep)
        inival.=solution
        plot(X,solution[1,:],
             title="time=$(@sprintf("%.4f",time))",
             xlabel="x",ylabel="y",
             ylims=(0,1))
        tstep*=dtgrowth
    end
end

In [ ]:
injupyter()&& convection_diffusion(n=40,tstep0=1.0e-3,D=0.01, v=10.0,centered=true,expfit=false)

In [ ]:
injupyter()&& convection_diffusion(n=40,tstep0=1.0e-3,D=0.01, v=10.0,centered=false,expfit=true)


For the small choosen diffusion coefficient, we observe a convection dominant transport to the right
end of the domain, where species start to "pile up". For the centered flux, unphysical oscillations
start to occur. For the exponential fitting flux, these are avoided at the price of additional
diffusion "smearing out" the solution.


### Nonlinear diffusion problem $\partial_t u - \nabla\cdot D\nabla u^m=0$

In [ ]:
function nonlinear_diffusion(;n=1000, nt=100, tstep0=1.0e-3, D=1.0, dtgrowth=1.0, m=3)

    # Grid on interval 0.1
    X=collect(0:1.0/n:1)
    grid=VoronoiFVM.Grid(X)

    function flux!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        f[1]=uk[1]^m-ul[1]^m
    end
    function storage!(f,u,node,data)
        f[1]=u[1]
    end

    # initial value with finite support
    fpeak(x)= 0.45≤ x ≤ 0.55 ? 1.0 : 0.0

    physics=VoronoiFVM.Physics(
        flux=flux!,
        storage=storage!)

    sys=VoronoiFVM.DenseSystem(grid,physics)
    enable_species!(sys,1,[1])
    inival=unknowns(sys)
    solution=unknowns(sys)
    inival[1,:].=map(x->fpeak(x),X)
    time=0.0
    tstep=tstep0
    @gif for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,tstep=tstep)
        inival.=solution
        plot(X,solution[1,:],
             title="time=$(@sprintf("%.4f",time))",
             xlabel="x",ylabel="y",
             ylims=(0,1))
        tstep*=dtgrowth
    end
end

In [ ]:
injupyter()&& nonlinear_diffusion(m=3)


For this example, we deliberately start with a solution with finite support.
In the case of $m>1$, we observe, that during the evolution, the finit support
property of the solution is conserved.

In [ ]:
function nonlinear_diffusion2D(;n=50, nt=100, tstep0=1.0e-3, D=1.0, dtgrowth=1.0, m=3)

    # Grid on interval 0.1
    X=collect(0:1.0/n:1)
    grid=VoronoiFVM.Grid(X,X)
    function flux!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        f[1]=uk[1]^m-ul[1]^m
    end
    function storage!(f,u,node,data)
        f[1]=u[1]
    end

    # initial value with finite support
    fpeak(x,y)= 0.45≤ x ≤ 0.55 &&  0.45≤ y ≤ 0.55 ? 1.0 : 0.0

    physics=VoronoiFVM.Physics(
        flux=flux!,
        storage=storage!)

    sys=VoronoiFVM.DenseSystem(grid,physics)
    enable_species!(sys,1,[1])
    inival=unknowns(sys)
    solution=unknowns(sys)
    for i=1:num_nodes(grid)
        inival[1,i]=fpeak(grid.coord[1,i],grid.coord[2,i])
    end
    time=0.0
    tstep=tstep0
    for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,tstep=tstep)
        inival.=solution
        p=contourf(X,X,reshape(solution[1,:],length(X),length(X)),levels=collect(0:0.1:1.0),
                 clim=(0,1.0),
                 colorbar=:right,color=:viridis,
                 title=@sprintf("time=%.4f\n",time))
        tstep*=dtgrowth
        gui(p)
    end
end

In [ ]:
injupyter()&& nonlinear_diffusion(m=3)


### Brusselator system

The Brusselator is a system of two species interacting via a reaction:

\begin{align*}
  \partial_t u_1 - \nabla \cdot D_1 \nabla u_1 + (B+1)u_1-A-u_1^2u_2  &=0\\
  \partial_t u_2 - \nabla \cdot D_2 \nabla u_2 + u_1^2u_2 -B u_1 &=0\\
\end{align*}

In [ ]:
function brusselator(;n=20,nt=150,tstep=0.05)
    A=4.0
    B=6.0
    D1=0.01
    D2=0.1
    perturbation=0.1;

    function diffusion!(f,u,edge,data)
        uk=viewK(edge,u)
        ul=viewL(edge,u)
        f[1]=D1*(uk[1]-ul[1])
        f[2]=D2*(uk[2]-ul[2])
    end

    function reaction!(f,u,node,data)
        x=u[1]
        y=u[2]
        f[1]= (B+1.0)*x-A-x*x*y
	f[2]= x*x*y-B*x
    end

    function storage!(f,u,node,data)
        f[1]=u[1]
        f[2]=u[2]
    end

    h=1.0/convert(Float64,n-1)
    X=collect(-1:h:1)
    Y=collect(-1:h:1)
    nx=length(X)
    ny=length(Y)
    grid=VoronoiFVM.Grid(X,Y)

    # Create a physics structure
    physics=VoronoiFVM.Physics(
        num_species=2,
        flux=diffusion!,
        storage=storage!,
        reaction=reaction!)

    sys=VoronoiFVM.DenseSystem(grid,physics)

    enable_species!(sys,1,[1])
    enable_species!(sys,2,[1])

    # Create a solution array
    inival=unknowns(sys)
    solution=unknowns(sys)
    t0=0

    for i=1:nx*ny
        inival[1,i]=1.0+perturbation*randn()
        inival[2,i]=1.0+perturbation*randn()
    end
    time=t0
    control=VoronoiFVM.NewtonControl()
    control.verbose=true
    control.max_lureuse=0
    control.tol_relative=1.0e-5
    control.tol_linear=1.0e-4
    @gif for i=1:nt
        time=time+tstep
        solve!(solution,inival,sys,control=control,tstep=tstep)
        inival.=solution
        @views begin
            p1=contourf(X,Y,reshape(solution[1,:],nx,ny),colorbar=:right,color=:viridis,aspect_ratio=1)
	    p2=contourf(X,Y,reshape(solution[2,:],nx,ny),colorbar=:right,color=:viridis,aspect_ratio=1)
            p=plot(p1,p2,layout=(1,2),title="time=$(time)" )
        end
        tstep*=1.05
    end
end

In [ ]:
injupyter()&& brusselator()

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*